## Preparing the data : 

In [20]:
jd_1 = pd.read_csv('./jobs_data/JD_data.csv') 

In [55]:
jd_1.columns

Index(['Unnamed: 0', 'ISCO', 'major_job', 'job', 'position', 'location',
       'description'],
      dtype='object')

In [59]:
jd_1 = jd_1[['description','position']].drop_duplicates() 

In [60]:
jd_2.columns

Index(['job_ID', 'job', 'location', 'company_id', 'company_name', 'work_type',
       'full_time_remote', 'no_of_employ', 'no_of_application',
       'posted_day_ago', 'alumni', 'Hiring_person', 'linkedin_followers',
       'hiring_person_link', 'job_details', 'Column1'],
      dtype='object')

In [21]:
jd_2 = pd.read_csv('./jobs_data/linkdin_Job_data.csv') 

In [62]:
jd_2 = jd_2[['job_details','job']].drop_duplicates() 

In [22]:
jd_3 = pd.read_csv('./jobs_data/monster_com-job_sample.csv') 

In [65]:
jd_3 = jd_3[['job_description','job_title']].drop_duplicates() 

In [79]:
jd_2 = jd_2.rename(columns={'job_details' : 'description', 'job' : 'position'}) 

In [83]:
jd_3 = jd_3.rename(columns={'job_description' : 'description', 'job_title' : 'position'}) 

In [119]:
jobs = pd.read_csv('job_descriptions.csv') 

In [120]:
jobs = jobs[['Job Description','Job Title']] 

In [121]:
jobs = jobs.rename(columns= { 'Job Description' : 'description', 'Job Title' : 'position' }) 

In [122]:
jobs = jobs.drop_duplicates()

In [118]:
jobs_nyc = pd.read_csv('./jobs_data/Jobs_NYC_Postings.csv') 

In [125]:
jobs_nyc = jobs_nyc[['Job Description','Business Title']] 

In [126]:
jobs_nyc = jobs_nyc.rename(columns= { 'Job Description' : 'description', 'Business Title' : 'position' }) 

In [184]:
n = 100

duplicated_df_1 = jd_1.loc[jd_1.index.repeat(n)]
duplicated_df_1 = duplicated_df_1.reset_index(drop=True)
duplicated_df_2 = jd_2.loc[jd_2.index.repeat(n)]
duplicated_df_2 = duplicated_df_2.reset_index(drop=True)
duplicated_df_3 = jd_3.loc[jd_3.index.repeat(n)]
duplicated_df_3 = duplicated_df_3.reset_index(drop=True)
duplicated_df_4 = jobs_nyc.loc[jobs_nyc.index.repeat(n)]
duplicated_df_4 = duplicated_df_4.reset_index(drop=True)

In [185]:
final_jobs = pd.concat([duplicated_df_1, duplicated_df_2, duplicated_df_3,jobs,duplicated_df_4], axis=0)

In [186]:
final_jobs

description  \
0       [' You have an academic degree in physics or e...   
1       [' You have an academic degree in physics or e...   
2       [' You have an academic degree in physics or e...   
3       [' You have an academic degree in physics or e...   
4       [' You have an academic degree in physics or e...   
...                                                   ...   
517295  The NYC Department of Environmental Protection...   
517296  The NYC Department of Environmental Protection...   
517297  The NYC Department of Environmental Protection...   
517298  The NYC Department of Environmental Protection...   
517299  The NYC Department of Environmental Protection...   

                                   position  
0             Accelerator Physicist id54315  
1             Accelerator Physicist id54315  
2             Accelerator Physicist id54315  
3             Accelerator Physicist id54315  
4             Accelerator Physicist id54315  
...                                     ...  
517295  2024-BWT-015-Process Support Intern  
517296  2024-BWT-015-Process Support Intern  
517297  2024-BWT-015-Process Support Intern  
517298  2024-BWT-015-Process Support Intern  
517299  2024-BWT-015-Process Support Intern  

[3394276 rows x 2 columns]

## Modeling 

In [187]:
from bertopic import BERTopic 

In [188]:
topic_model = BERTopic() 

In [189]:
import pandas as pd

In [190]:
final_jobs = final_jobs[final_jobs['description'].apply(lambda x: type(x) != float)]


In [191]:
def clean_job(job) : 
    clean_job = job
    unwated_words=  ['and',
 'of',
 'to',
 'in',
 'the',
 'for',
 'with',
 'experience',
 'or',
 'is',
 'as',
 'on',
 'our',
 'work',
 'be',
'an',
'are',
'will',
'you',
'we',
'have',
                    ]
    for word in unwated_words : 
        clean_job = clean_job.replace(word,' ') 
    return clean_job

In [192]:
final_jobs['description'] = final_jobs['description'].apply(lambda x : x.replace('[','').replace(']','')) 

In [193]:
final_jobs['description'] = final_jobs['description'].apply(clean_job) 

In [ ]:
from bertopic import BERTopic
from hdbscan import HDBSCAN

hdbscan_model = HDBSCAN(min_cluster_size=20, metric='euclidean', 
                        cluster_selection_method='eom', prediction_data=True, min_samples=10)
topic_model = BERTopic(hdbscan_model=hdbscan_model,top_n_words=15,min_topic_size=100)
topics, probs = topic_model.fit_transform(final_jobs['description'])

## Testing 

In [4]:
loaded_model = BERTopic.load("path/to/my/model_dir")


In [176]:
topic_model.get_topic_info(-1)['Representation'][0]

['bus',
 'ess',
 'sales',
 'al',
 'skills',
 'cus',
 'data',
 'ce',
 'agement',
 'team',
 'comp',
 'market',
 'soluti',
 'supp',
 'per']

In [174]:
topic_model.visualize_topics()

### Coherence score 

In [146]:
!pip install smart_open


[notice] A new release of pip is available: 23.1.2 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip


In [147]:
import gensim.corpora as corpora
from gensim.models.coherencemodel import CoherenceModel
vectorizer = topic_model.vectorizer_model
analyzer = vectorizer.build_analyzer()
tokens = [analyzer(doc) for doc in jobs["Job Description"]]
dictionary = corpora.Dictionary(tokens)
corpus = [dictionary.doc2bow(token) for token in tokens]
topics = topic_model.get_topics()
topics.pop(-1, None)
topic_words = [
    [word for word, _ in topic_model.get_topic(topic) if word != ""] for topic in topics
 ]
topic_words = [[words for words, _ in topic_model.get_topic(topic)] 
            for topic in range(len(set(topics))-1)]

 # Evaluate
coherence_model = CoherenceModel(topics=topic_words, 
                              texts=tokens, 
                              corpus=corpus,
                              dictionary=dictionary, 
                              coherence='c_v')
coherence = coherence_model.get_coherence()

ModuleNotFoundError: No module named 'smart_open.compression'

### Individual interpretations

#### Testing on jobs

In [148]:
test_examples = ["""Develop, implement, and maintain leading-edge analytics systems, taking complicated problems and building simple frameworks
Identify trends and opportunities for growth through analysis of complex datasets
Evaluate organizational methods and provide source-to-target mappings and information-model specification documents for datasets
Create best-practice reports based on data mining, analysis, and visualization
Evaluate internal systems for efficiency, problems, and inaccuracies, and develop and maintain protocols for handling, processing, and cleaning data
Work directly with managers and users to gather requirements, provide status updates, and build relationships
Responsibilities
Work closely with project managers to understand and maintain focus on their analytics needs, including critical metrics and KPIs, and deliver actionable insights to relevant decision-makers
Proactively analyze data to answer key questions for stakeholders or yourself, with an eye on what drives business performance, and investigate and communicate which areas need improvement in efficiency and productivity
Create and maintain rich interactive visualizations through data interpretation and analysis, with reporting components from multiple data sources
Define and implement data acquisition and integration logic, selecting an appropriate combination of methods and tools within the defined technology stack to ensure optimal scalability and performance of the solution
Develop and maintain databases by acquiring data from primary and secondary sources, and build scripts that will make our data evaluation process more flexible or scalable across datasets
Required skills and qualifications
Three or more years of experience mining data as a data analyst
Proven analytics skills, including mining, evaluation, and visualization
Technical writing experience in relevant areas, including queries, reports, and presentations
Strong SQL or Excel skills, with aptitude for learning other analytics tools
Preferred skills and qualifications
Bachelor’s degree (or equivalent) in mathematics, computer science, economics, or statistics
Experience with database and model design and segmentation techniques
Strong programming experience with frameworks, including XML, JavaScript, and ETL
Practical experience in statistical analysis through the use of statistical packages, including Excel, SPSS, and SAS
Proven success in a collaborative, team-oriented environment""","""  Write well designed, testable, efficient code by using best software development practices
Create website layout/user interface by using standard HTML/CSS practices
Integrate data from various back-end services and databases
Gather and refine specifications and requirements based on technical needs
Create and maintain software documentation
Be responsible for maintaining, expanding, and scaling our site
Stay plugged into emerging technologies/industry trends and apply them into operations and activities
Cooperate with web designers to match visual design intent
Requirements and skills
Proven working experience in web programming
Top-notch programming skills and in-depth knowledge of modern HTML/CSS
Familiarity with at least one of the following programming languages: PHP, ASP.NET, Javascript or Ruby on Rails
A solid understanding of how web applications work including security, session management, and best development practices
Adequate knowledge of relational database systems, Object Oriented Programming and web application development
Hands-on experience with network diagnostics, network analytics tools
Basic knowledge of Search Engine Optimization process
Aggressive problem diagnosis and creative problem solving skills
Strong organizational skills to juggle multiple tasks within the constraints of  timelines and budgets with business acumen
Ability to work and thrive in a fast-paced environment, learn rapidly and master diverse web technologies and techniques.
BS in computer science or a related field""",""" As a Creative Designer at Yamaha Lifestyle Zone - New Chen Motor Credit Sdn Bhd, you will be responsible for creating visually appealing digital content and posters, developing a strong brand identity that aligns with Yamaha's branding, and designing engaging and attractive banners and booth setups for roadshows and physical marketing events. You will also assist in all marketing department activities and actively participate in company scheduled motorsports activities and team events.

Key Responsibilities:

Develop and maintain a cohesive brand identity for New Chen Motor Credit Sdn Bhd in line with Yamaha's branding guidelines.
Create visually appealing digital content and posters for online and offline marketing campaigns.
Design engaging and attractive banners and booth setups for roadshows and physical marketing events.
Collaborate with marketing and sales teams to understand project requirements and objectives.
Utilize photography and videography skills to capture high-quality product images and videos.
Stay updated on social media trends and emerging design techniques to keep our content fresh and relevant.
Produce multimedia content for various digital platforms, including social media, websites, and email campaigns.
Ensure all designs are consistent with our brand image and message.
Maintain organized files and records of design assets.
Assist in all marketing department activities to support overall marketing efforts.
Actively participate in company scheduled motorsports activities and team events to promote the brand and engage with customers.
Qualifications:

Bachelor's degree in Graphic Design, Multimedia Design, or a related field (or equivalent experience).
Proven experience as a Creative Designer or similar role.
Proficiency in graphic design software such as Adobe Creative Suite (Photoshop, Illustrator, InDesign, etc.).
Strong photography and videography skills with the ability to capture and edit high-quality images and videos.
A keen eye for detail and a passion for creativity and design.
Knowledge of current social media trends and digital marketing strategies.
Excellent communication and teamwork skills.
Strong organizational and time management abilities.
Ability to work independently and take initiative."""]  

In [178]:
res = topic_model.transform(test_examples) 

C:\Users\rayen\spark_env\Lib\site-packages\scipy\sparse\_index.py:145: SparseEfficiencyWarning:

Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.



In [179]:
res

([136, -1, -1], array([0.65908531, 0.        , 0.        ]))

#### Testing on profiles 

In [180]:
profiles = ["""Education : related courses : 
- statistical analysis 
- machine learning 
- deep learning 
- cloud services  
- probability and statistics 
Experience : 
machine learning intern : 
● Identified business challenges and opportunities within the recruitment process and applied Natural Language
Processing techniques to develop an innovative Application Tracking System. This system efficiently ranked
candidates for specific job descriptions, using named entity recognition and word embedding, resulting in a
significant reduction in the time spent on candidate selection.
● Orchestrated a comprehensive data acquisition strategy to harvest and preprocess candidate application data
with precision.
● Collaborated closely with HR and engineering teams to deploy the system using FastAPI and Vue.js, ensuring a
user-friendly interface for recruiters, and precisely mapped out a plan for the next 2 upcoming versions and
enhancements.
Buisness developer at enactus fst el manar : 
●Contributed to product creation, market evaluation, and customer segmentation while driving
clients' behavior analysis.
● Collaborated effectively with the sales team to develop a robust sales strategy for optimal results in 2 different
projects : Moonray, and Student plus
Junior machine learning engineer at omdena : 
● Played a pivotal role in the successful development and deployment of a computer vision system using deep
learning techniques ( pytorch ) in Egyptian orphanages, effectively tackling the issue of constrained monitoring.
● Gained expertise in deploying accurate solutions with low computational capabilities using python.
● Helped improve the well-being of more than 220 children.
Data analyst : omdena : 
● Successfully extracted and delivered actionable insights from a diverse dataset as part of the Omdena initiative for Peru's Open Data Platform, enabling positive transformation in Lima and significantly enhancing the quality of life for its residents. 
● Applied Python techniques for data collection and preprocessing, and Power BI for visualization dashboards, yielding critical insights into aggression trends and contributing to targeted interventions in Lima.
IT consultant at optima junior entreprise:  
● Utilized Vue.js, Laravel, and MySQL to successfully aggregate diverse data sources, standardize data storage, and develop interactive dashboards, leading to enhanced data management efficiency, elevated data quality, and user-friendly data accessibility.
Data science unity manager engineers spark : 
● Contributed To building a training strategy In the field of Data science for college students. 
● Executed 7 training sessions which significantly elevated students' proficiency in data science, achieving a remarkable 60% knowledge enhancement, coupled with an impressive satisfaction rate exceeding 85%.
Projects : 
Student performance prediction and analysis : 
Utilized and combined various machine learning techniques such as bagging and boosting with Python to predict
the performance of high school students.
● Employed Local and global interpretation techniques with Python to conduct in-depth analysis of the
inter-relations among various educational factors for performance prediction.
● Conducted A/B testing on a cohort of 1000 high school students to assess the impact of different educational
interventions and refine performance prediction models. 
Sales analysis : 
This project analyzes sales data with 3 interactive and clear dashboards. It summarizes sales indicators, highlights customer preferences, and details product categories/specifications driving valuable insights to inform business decisions. 
Virtual accounting firm : 
The platform aims to automate a workflow using angular. Additionally, it allows for better tracking of the accounting firm's resources and ensures more accurate and transparent billing for clients. It operates as a virtual office. Therefore, the principle is to automate various tasks that are typically performed in a "physical" office.""",
""" Automation Testing,"Technical Skills Summary I have completed ""CORPORATE TRAINING in Manual and Automation Testing"" at Source-Code Technology, Pune. â Manual and Automation Testing â¢ SELENIUM IDE, TestNG, SELENIUM Grid, JENKINS, Apache POI. â¢ Good knowledge in SDLC. â¢ Excellent understanding of White Box Testing and Black Box Testing. â¢ Good knowledge in Functional Testing, Integration Testing and System Testing. â¢ Good Exposure in writing Functional and Integration Scenarios. â¢ Good understanding of writing of test cases including test case design technique. â¢ Good understanding Build and release. â¢ Good knowledge on Ad hoc and smoke testing. â¢ Excellent understanding of usability, reliability and exploratory testing. â¢ Excellent knowledge of Globalization and Compatibility Testing. â¢ Excellent Understand of STLC. â¢ Good knowledge of regression and retesting. â¢ Excellent knowledge on Defect tracking and Defect Life Cycle. â¢ Good Knowledge on Test plan and Traceability Matrix. Internship Project Project Name: Resume Extractor Duration: 6 months Role: Manual And Automation Testing Environment: Jdbc, Servlets, Jsp, Technologies: Web based Application, MS Access2007 The project involved development of a web application. Resume extractor provides the technology to analyze mass volume of data to detect resume in data covered which company have into valuable information. This project is company site's based on recruitment process. Strengths â¢ Able to work in a team â¢ System and Operational Analysis â¢ Good Communication Skills â¢ Active learning and critical thinking â¢ Good interpersonal skills, willing to take challenges and more responsibilities. â¢ Ability to learn new technologies with minimal time period. Education Details 
January 2015  BCS Computer Science  MGM's College
 MCA  Pune, Maharashtra Computer Science fromJSPM College
 HSC  Nanded, Maharashtra Maharashtra state board
 SSC  Nanded, Maharashtra Maharashtra State Board
Software testing 

Software testing
Skill Details 
APACHE- Exprience - 6 months
BLACK BOX- Exprience - 6 months
BLACK BOX TESTING- Exprience - 6 months
FUNCTIONAL TESTING- Exprience - 6 months
INTEGRATION- Exprience - 6 monthsCompany Details 
company - Tech Mahindra
description - Software testing in manual and Automation
company - 
description - software Test engineer""","""DevOps Engineer,"Software Proficiency: â¢ Languages: Basics of C, SQL, PL/SQL,JAVA,JAVAEE,Javascript,HTML,CSS,jquery,mysql,Spring ,Hibernate. â¢ Software Tools: Xillinx, Modelsim, Matlab, Multisim. â¢ Operating Systems: Windows XP, Vista, 07, 08, Ubuntu. Project Profile: B.E. Project FPGA Implementation of Team Size: 4. Role: Programmer. AES Algorithm AES is Advanced Encryption Standard which is used in cryptography by which we can protect our data. It encrypted by a Secret Key. T.E. project Sorting Robot. Team Size: 3. Role: Mechanism designer. The TCS 230 sensor sorts the RGB color balls according to their color. Diploma Project RFID Based Student Team Size: 4. Role: Interface. Attendance System Using GSM. In this student show RFID card of his own and then message send via GSM to their parent that his ward is present.Education Details 
May 2016 B.E. Savitribai Phule Pune, Maharashtra Pune University
March 2010 S.S.C   Maharashtra Board
DevOps Engineer 


Skill Details 
C- Exprience - 6 months
C++- Exprience - 6 months
Sql- Exprience - 6 months
Pl/Sql- Exprience - 6 months
Core Java- Exprience - 6 months
Javascript- Exprience - Less than 1 year months
HTML- Exprience - Less than 1 year months
CSS- Exprience - Less than 1 year months
Jquery- Exprience - Less than 1 year months
JavaEE- Exprience - Less than 1 year months
Mysql- Exprience - Less than 1 year months
Python- Exprience - 6 monthsCompany Details 
company - Parkar Consulting and Labs
description - I'm working on the DevOps team in Parkar Consulting and Labs. I have hands on the AWS as well as Python"""] 


In [181]:
res = topic_model.transform(profiles) 

In [182]:
res[0] 

[74, -1, -1]

In [19]:
loaded_model.get_topic(275)

NameError: name 'loaded_model' is not defined

Interpretation : validated check 

In [135]:
loaded_model.get_topic(102)

[['suites', 0.12156514880941474],
 ['automate', 0.12156514880941474],
 ['test', 0.1070644785834111],
 ['testing', 0.09482001748489632],
 ['scripts', 0.07477053902923657],
 ['streamline', 0.07428483573839464],
 ['automated', 0.0622758551730547],
 ['automation', 0.062155569064783596],
 ['tools', 0.05357477249696042],
 ['using', 0.05022463691777485],
 ['efforts', 0.03575431972702465],
 ['engineers', 0.02729745487394001],
 ['efficiency', 0.027257857586007787],
 ['processes', 0.025779509623284732],
 ['enhance', 0.023787764625787366]]

In [140]:
qa_testing_ = get_similar_items(102) 

In [143]:
qa_testing_['Job Title'].value_counts()

Job Title
Software Tester              6852
Quality Assurance Analyst    3540
QA Analyst                   3527
Name: count, dtype: int64

Interpretation : validation check 

In [145]:
loaded_model.get_topic(381)

[['tasked', 0.06317954573174922],
 ['core', 0.06317954573174922],
 ['smoothly', 0.06317954573174922],
 ['efficiently', 0.06317954573174922],
 ['runs', 0.06317954573174922],
 ['logic', 0.050790501946738856],
 ['application', 0.04665901357447944],
 ['serverside', 0.04657768008886038],
 ['storage', 0.046526887719788794],
 ['building', 0.04308107547457145],
 ['server', 0.04035145046396734],
 ['backend', 0.037763010316526506],
 ['developer', 0.029304712164645533],
 ['database', 0.029298738213526784],
 ['functionality', 0.026818204887960672]]

In [146]:
devops = get_similar_items(381) 

In [147]:
devops['Job Title'].value_counts()

Job Title
Software Engineer     10404
Web Developer          6798
Back-End Developer     3499
Name: count, dtype: int64

Since that the skills mentionned in the profile are varied, and our model is quite precise in the topic selection, the given topics are not very broad from the topic of the profile. We may overcome this problem by tolerating the recommendation of the first k matching topics later in the matching algorithm. 